In [1]:
from obspy import read
import matplotlib.pyplot as plt
import obspy
from obspy.clients.fdsn import Client
from obspy import UTCDateTime
from obspy.core import AttribDict
from obspy.io.sac import SACTrace
import numpy as np
import matplotlib.pylab as plt
import os
import pandas as pd
import shutil
from tqdm import tqdm
import warnings
from obspy import read_inventory, UTCDateTime
from obspy.core.inventory import Inventory, Network, Station, Channel, Site

In [13]:
network = "G" # YO ENAM; ZA NoMelt
tstart = "2001-12-02T00:00:00"
tend = "2002-11-25T23:59:59"

comps = ['BHZ','BH1','BH2'] #['BHZ','BH1','BH2','BDH'] #["HXZ", "HX1", "HX2"] #["LHZ", "LH1", "LH2"] #["HHZ", "HH1", "HH2"] #["HHZ", "HH1", "HH2", "BDH"]
outunits = 'DISP' # DISP, VEL, ACC [For pressure channels, should use "VEL"] 
client = Client('IRIS')
stations = "*"
# If you want to specify the stations
#stations = ('A01','A03','A05', 'A07', 'A09', 'A11', 'A13', 'B02', 'B03', 'B06', 'B08', 'B10', 'B12', 'B13', 'C02', 'C04', 'C06', 'C12', 'C13', 'C15', 'F01')
#stations = ','.join(stations)

t1 = UTCDateTime(tstart)
t2 = UTCDateTime(tend)

# STATIONS
inventory = client.get_stations(network=network, station=stations,channel=comps[0], level='response')#starttime=t1, endtime=t2, 
print(inventory)


Inventory created at 2023-08-01T17:55:33.759800Z
	Created by: IRIS WEB SERVICE: fdsnws-station | version: 1.1.52
		    http://service.iris.edu/fdsnws/station/1/query?network=G&station=%2...
	Sending institution: IRIS-DMC (IRIS-DMC)
	Contains:
		Networks (1):
			G
		Stations (47):
			G.AIS (Nouvelle-Amsterdam - TAAF, France)
			G.ATD (Arta Cave - Arta, Republic of Djibouti)
			G.CAN (Canberra, Australia)
			G.CCD (Concordia Base, Dome C, Antartica)
			G.CLF (Chambon la Foret Observatory, France)
			G.COYC (Coyhaique, Chile)
			G.CRZF (Port Alfred - Ile de la Possession - Crozet Islands, France)
			G.DRV (Dumont d'Urville - Terre Adelie, Antarctica)
			G.DZM (Dzumac - New Caledonia, France)
			G.ECH (Echery - Sainte Marie aux Mines, France)
			G.EDA (Edea, Cameroon)
			G.EVO (Evora, Portugal)
			G.FDF (Fort de France - Martinique island, France)
			G.FDFM (Morne la Rosette, Martinique, France)
			G.FOMA (Nahampoana Reserve - Fort Dauphin, Madagascar)
			G.FUTU (Maopo'opo, Futuna)
			G.GR

In [14]:
#remove response for all downloaded files in a network

#the folder where all downloaded files in a network located
#folder_path = '/gpfs/fs2/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/script_for_download_parallelly/output/YY/YY'
folder_path = '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G'
#the folder that store all files in a network after removing response. You need to create this folder first.
output_folder = '/gpfs/fs2/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/removed_response_output/G'

sac_files = []

# loop through all station folders in the network folder
for station_folder in os.listdir(folder_path):
    station_folder_path = os.path.join(folder_path, station_folder)
    for root, dirs, files in os.walk(station_folder_path):
        # loop through all files in the station folder
        for file in files:
            if file.endswith(".sac"):
                # add file to sac_files list
                sac_files.append(os.path.join(root, file))

# count files that need to remove response
count = len(sac_files)
print(count)

#progress bar
pbar = tqdm(total=len(sac_files))

# list to store files with errors
abnormal_sac_files = []

# Load all SAC files in sac_files list using ObsPy
for sac_file in sac_files:
    try:
        st = read(sac_file)
        st.attach_response(inventory)
        st.remove_response(inventory=inventory)

        # Create output station folders
        relative_path = os.path.relpath(os.path.dirname(sac_file), folder_path)
        output_subfolder = os.path.join(output_folder, relative_path)
        os.makedirs(output_subfolder, exist_ok=True)

        # Generate output file path
        # Output files will have the same names as the original files
        output_file_name = os.path.basename(sac_file)
        output_file_path = os.path.join(output_subfolder, output_file_name)
        
        # Check if the output file already exists
        if os.path.exists(output_file_path):
            print(f"Skipping '{sac_file}': File already exists in the output folder.")
            continue
            
        # Write the modified stream to the output file path
        st.write(output_file_path, format="SAC")
        pbar.update(1)
        
    #If there's an error when removing response, skip that file and continue            
    except ValueError as e:
        print(f"Skipping '{sac_file}': {str(e)}")
        abnormal_sac_files.append(sac_file)
        
        #If there's an error when removing response, copy the file as it is to new folder
        #error_file_path = os.path.join(output_subfolder, output_file_name)
        #shutil.copy(sac_file, error_file_path)
        #print(f"Original file copied to '{error_file_path}'")
        continue
                 
# Close the progress bar
pbar.close()

print("Files with errors:")
print(abnormal_sac_files)

46185


  0%|          | 1/46185 [00:00<9:13:38,  1.39it/s]

Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/FUTU_G/FUTU_G.2020.240.00.00.00.BHZ.sac': File already exists in the output folder.


  0%|          | 7/46185 [00:03<4:59:17,  2.57it/s]

Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/FUTU_G/FUTU_G.2019.128.00.00.00.BHZ.sac': File already exists in the output folder.


...

Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.2007.016.00.00.00.BH2.sac': No matching response information found.


 58%|█████▊    | 26663/46185 [2:41:24<57:47,  5.63it/s]

Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.2003.006.00.00.00.BH1.sac': No matching response information found.
Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.2005.129.00.00.00.BH2.sac': No matching response information found.
Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.1994.016.00.00.00.BH1.sac': No matching response information found.
Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.2005.168.00.00.00.BH2.sac': No matching response information found.


 58%|█████▊    | 26665/46185 [2:41:24<1:58:09,  2.75it/s]

Skipping '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PPT_G/PPT_G.2005.174.00.00.00.BH2.sac': No matching response information found.
Files with errors:
['/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.2002.333.00.00.00.BH2.sac', '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.2001.089.00.00.00.BH1.sac', '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.2002.245.00.00.00.BH2.sac', '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.1998.156.00.00.00.BH1.sac', '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.2000.203.00.00.00.BH2.sac', '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_BHZ12/G/G/PVC_G/PVC_G.2002.233.00.00

In [16]:
# Troubleshooting for abnormal_sac_files
# Use this part if you want to look at info of specific channel/station/network
network = "YL"
station = 'B03'

# Download the specific response from an online source
client = Client("IRIS")
inventory_specific = client.get_stations(network=network,station=station,channel='BHZ', level="response")

# Channel info for reference
inventory_specific[0][0][0] #[0] for station info and [0][0] for network info

Channel 'BHZ', Location '' 
	Time range: 2009-11-27T20:28:54.000000Z - 2010-11-27T06:43:47.000000Z
	Latitude: -19.9414, Longitude: -175.3855, Elevation: -2015.0 m, Local Depth: 0.0 m
	Azimuth: 0.00 degrees from north, clockwise
	Dip: 90.00 degrees down from horizontal
	Channel types: GEOPHYSICAL
	Sampling Rate: 40.00 Hz
	Sensor (Description): None (LDEO OBS Sensor Mk2/LDEO_new dummy at 40/125)
	Response information available

In [30]:
# If you want to enter abnormal_sac_files by hand
abnormal_sac_files = ['/gpfs/fs2/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_island/IU/IU/PTCN/PTCN.2002.043.00.00.00.BHZ.sac',
                      '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_island/IU/IU/AFI/AFI.2001.335.00.00.00.BHZ.sac',
                     '/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/island_networks/output_island/II/II/MSVF/MSVF.2018.106.00.00.00.BHZ.sac']

In [33]:
# See the date of the first file in abnormal_sac_files to fill 'time' variable below.
st = read(abnormal_sac_files[0],format="SAC")
print(st)

1 Trace(s) in Stream:
IU.PTCN.01.BHZ | 2002-02-12T00:00:00.021097Z - 2002-02-12T23:59:59.521097Z | 2.0 Hz, 172800 samples


In [72]:
# Create an inventory for a abnormal sac file manually, and use this inventory to remove response
network = '7B'
station = 'SM05'
station_code = network+'.'+station+'..'+'BHZ'
time = "2019-11-26T00:00:00" # It is the best to use a dates close to the abnormal date, which are the most likely one to have response.

client = Client("IRIS")
inventory_specific = client.get_stations(network=network,station=station,channel='BHZ', level="response")
latitude = inventory_specific[0][0].latitude
longitude = inventory_specific[0][0].longitude
elevation = inventory_specific[0][0].elevation
depth = inventory_specific[0][0][0].depth
azimuth = inventory_specific[0][0][0].azimuth
dip = inventory_specific[0][0][0].dip
sample_rate = inventory_specific[0][0][0].sample_rate

# We'll first create all the various objects. These strongly follow the
# hierarchy of StationXML files.
inv = Inventory(
    # We'll add networks later.
    networks=[],
    # The source should be the id whoever create the file.
    source="URSeismo-OBS")

net = Network(
    # This is the network code according to the SEED standard.
    code=network,
    # A list of stations. We'll add one later.
    stations=[],
    description="manually_remove_response_inventory",
    # Start-and end dates are optional.
    #start_date=obspy.UTCDateTime(2016, 1, 2)
)

sta = Station(
    # This is the station code according to the SEED standard.
    code=station,
    latitude=latitude,
    longitude=longitude,
    elevation=elevation,
    #creation_date=obspy.UTCDateTime(2016, 1, 2),
    site=Site(name=station))

cha = Channel(
    # This is the channel code according to the SEED standard.
    code="BHZ",
    # This is the location code according to the SEED standard.
    location_code="",
    # Note that these coordinates can differ from the station coordinates.
    latitude=latitude,
    longitude=longitude,
    elevation=elevation,
    depth=depth,
    azimuth=azimuth,
    dip=dip,
    sample_rate=sample_rate)

# By default this accesses the NRL online. Offline copies of the NRL can
# also be used instead
nrl = client.get_stations(network=network,station=station,channel='BHZ', level="response")
# The contents of the NRL can be explored interactively in a Python prompt,
# see API documentation of NRL submodule:
# http://docs.obspy.org/packages/obspy.clients.nrl.html
# Here we assume that the end point of data logger and sensor are already
# known:
datetime = UTCDateTime(time)
response = nrl.get_response(station_code, datetime)


# Now tie it all together.
cha.response = response
sta.channels.append(cha)
net.stations.append(sta)
inv.networks.append(net)

# And finally write it to a StationXML file. We also force a validation against
# the StationXML schema to ensure it produces a valid StationXML file.
#
# Note that it is also possible to serialize to any of the other inventory
# output formats ObsPy supports.
inv.write("station.xml", format="stationxml", validate=True)


In [12]:
# Use the .xml file created above to remove response
network = 'IU'
station = 'PTCN'
#the folder that store abnormal sac files in a network after removing response. You need to create this folder first.
output_folder = '/gpfs/fs2/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/removed_response_output/IU/'+station
inventory = read_inventory("station.xml")
st.attach_response(inventory)
for file in abnormal_sac_files:
    try:
        # Read the SAC file
        st = read(file)

        # Remove instrument response
        st.attach_response(inventory)
        st.remove_response(inventory=inventory)
        
        print('Successfully removed response for the following abnormal sac file:')
        print(st)
        
        # Save the processed data 
        filename = os.path.basename(file)
        output_file = os.path.join(output_folder, filename)
        st.write(output_file, format='SAC')
        
        # Delete the file from the abnormal_sac_file list
        abnormal_sac_files.remove(file)
        
    except ValueError as e:
        print(f"Skipping '{file}': {str(e)}")
        continue

FileNotFoundError: [Errno 2] No such file or directory: 'station.xml'

In [29]:
# Test if a sac file is normal
# If it's normal it will print out info of the file, otherwise error 'No maching response' will occur
st = read('/gpfs/fs2/scratch/tolugboj_lab/Prj4c_OJP/2_Data/OJ/fetch_NOISE-master/output/YL/YL/B02/B02.2009.331.00.00.00.BHZ.sac', format="SAC")

print(st)

1 Trace(s) in Stream:
YL.B02..BHZ | 2009-11-27T00:00:00.023000Z - 2009-11-27T23:59:59.023000Z | 1.0 Hz, 86400 samples
